Welcome to my notebook.


**Edit this URL so that it points to *your* home**

<https://hub.xpub.nl/chopchop/~MYUSERNAME/magick/>

for instance:

<https://hub.xpub.nl/chopchop/~murtaugh/magick/>

## Bash in a notebook

There are two ways to include BASH (or shell) commands in a jupyter notebook. The simplest is just with an exclamation mark as the first character.

In [3]:
! convert

Version: ImageMagick 6.9.11-60 Q16 arm 2021-01-25 https://imagemagick.org
Copyright: (C) 1999-2021 ImageMagick Studio LLC
License: https://imagemagick.org/script/license.php
Features: Cipher DPC Modules OpenMP(4.5) 
Delegates (built-in): bzlib djvu fftw fontconfig freetype heic jbig jng jp2 jpeg lcms lqr ltdl lzma openexr pangocairo png tiff webp wmf x xml zlib
Usage: convert-im6.q16 [options ...] file [ [options ...] file ...] [options ...] file

Image Settings:
  -adjoin              join images into a single multi-image file
  -affine matrix       affine transform matrix
  -alpha option        activate, deactivate, reset, or set the alpha channel
  -antialias           remove pixel-aliasing
  -authenticate password
                       decipher image with this password
  -attenuate value     lessen (or intensify) when adding noise to an image
  -background color    background color
  -bias value          add bias when convolving an image
  -black-point-compensation
               

In [ ]:
You can also include multiple lines of bash with the "magicword" format:

In [6]:
%%bash
for x in *
do
echo I see $x
done

I see split_and_stitch.ipynb


## Imagemagick

We will be making use of imagemagick. The main website for the software is:

https://imagemagick.org/


## Get an image

Using wget, from the [archive of Guttorm Guttormsgaard](https://arkiv.guttormsgaardsarkiv.no/). We are going to be working with [an image from El Lissitzky's book: For the Voice](https://arkiv.guttormsgaardsarkiv.no/node/290/item/39) published in Berlin in 1923. It's a collaboration with poet Vladimir Mayakovsky. You can also find a PDF of the book in [archive.org](https://archive.org/details/vladimir-majakovskij-el-lissitzky-dlja-golosa-1923), where it is claimed:

> Famous collection of 13 poems by Majakovskij typographically translated by El Lissitzky. These poems were thought to be read out loud and from this the title (“For the Voice”).


In [8]:
! curl https://arkiv.guttormsgaardsarkiv.no/media/media/13d_MG_0121WEB.jpg --output 13d_MG_0121WEB.jpg

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 2555k  100 2555k    0     0  2116k      0  0:00:01  0:00:01 --:--:-- 2119k


We can use *ls* to get some generic information about the image we just downloaded...

In [ ]:
! ls -hl *.jpg

But imagemagick provides a command called *identify* that can give more specific information about images.

In [9]:
! identify *.jpg

13d_MG_0121WEB.jpg JPEG 2880x2218 2880x2218+0+0 8-bit sRGB 2.49599MiB 0.000u 0:00.004


## Read/Make the manual!

The *main* command of imagemagick is *convert*. You can run it to see some information.

In [ ]:
! convert

You can also have a look at the man page, with the *man* command.

In [ ]:
! man convert

Here's a very useful pipeline (two commands put together) that make a PDF from the manual page. [See the wiki!](https://pzwiki.wdka.nl/mediadesign/Man_page)

In [ ]:
! man -t convert | ps2pdf - > convert.pdf

As nice as the PDF is however, it's not complete. They don't call imagemagick the *swiss army knife* of images for nothing! We'll also need to use some online documentation. I really like this page: https://imagemagick.org/Usage/

## Make a working image no more than 1000x wide

The image we have is pretty high resolution, to make working with it easier and faster, let's make smaller size. Convert has a lot of sub-commands that are all accessed by naming them with a "-" before the name. This follows a convention of seeing the subcommands as *options*. After -convert, the command expects / requires additional information (which can be called the "argument"). These are all specific to the particular subcommnd. Convert can take an image size given in the form WIDTHxHEIGHT. But a convenient trick is that you can just give the WIDTH or the HEIGHT and imagemagick will figure it out.

In [10]:
! convert -resize 1000x 13d_MG_0121WEB.jpg 13d_MG_0121WEB.1000x.jpg

If you wanted an image that was 1000 pixels high (and whatever width necessary to keep the aspect ratio), how might you do that?

In [ ]:
! convert -resize SOMETHINGELSEHERE ANOTHERNAME.jpg

## Use crop to split your image

The [crop](https://imagemagick.org/Usage/crop) command can do *many things*... Try changing the numbers and see if it makes sense what's happening...

In [11]:
! convert -crop 200x200+500+0 13d_MG_0121WEB.1000x.jpg crop_numbers.jpg

Imagemagick has a unique idea of [geometry](https://imagemagick.org/Usage/basics/#arg_geometry) a really flexible, but initially confusing, way to specify both a SIZES and POSITIONS in an image; this flexible format is used by a number of commands, including *crop*

> All the following string forms are understood the geometry argument parser...
>
>    WxH+X+Y   WxH   +X+Y   A   A/B/C   A,B,C,D,E 

There's also a notion of "gravity" that can be values likeCenter, South, North, East, West....

In [ ]:
! convert 13d_MG_0121WEB.1000x.jpg -gravity Center -crop 500x500+0+0 +repage  crop_center.jpg

You can also use percentages to do interesting splits.

In [ ]:
! convert -crop 50%x+0+0 13d_MG_0121WEB.1000x.jpg crop_half.jpg

Actually I wanted the whole left half of the book, how to make it work ???!

## SPLIT into tiles

According to [the docs](https://imagemagick.org/Usage/crop/#crop_tile), the crop command can also do "tile cropping"...

> One of the more useful aspects of crop is when you don't give a specific position to the crop command. That is, you give a size, and not a position within the image to crop. In this case instead of generating just one image, crop generates a whole series of images.. 

In [ ]:
! convert -crop 128x128 Warren_Brodey_Earthchild_Book1_HighRes_10.1000x.jpg tiles/tile%02d.jpg

Oops, the output name expects there to already be a folder called tiles, better make it (with *mkdir*) and *try again*!!!

In [ ]:
! mkdir -p tiles

## STITCH your image back together as a GIF

In [ ]:
! convert tiles/*.jpg tiles.gif

Nice! I wonder if you could make a width GIF that scans vertically across the page ?

## Reassemble your image as a web page

In [ ]:
! ls tiles/* >> tiles.html

If all goes well you should see a new file: *tiles.html*  
Whoa! What just happened...

The >> means "append to file" ... Append just means add to the end of a file. If a file doesn't exist, it gets created, otherwise, it will add to it.

So, you made a file called ".html", but actually it doens't really have any markup.

* Try opening the file here "inside jupyter",  
* Try opening the file OUTSIDE of jupyter (via your public_html link)  
* Try right-clicking the file to open it in an editor.

Now for the tricky part, 

Try editing the file to add HTML, ie...

```html
<img src="tiles/tile1.jpg">
```

BUT... instead of hand editing each line... you can try to use "multi-cursor" mode of the jupyter text editor. Normally, you can make multiple cursors by pressing the CTRL+ALT keys and then select all the lines. Make sure you start at the beginning of the line, type the first part, then to jump to the end, you might use the "End" key (if you have one) or whatever shortcut your system uses to jump to the end of a line. Then type the rest...

## Publish me!

In [4]:
! jupyter-nbconvert split_and_stitch.ipynb --to html

[NbConvertApp] Converting notebook split_and_stitch.ipynb to html
[NbConvertApp] Writing 318292 bytes to split_and_stitch.html
